# Neighborhood Computations

In [7]:
import numpy as np
import igl
import math
import meshplot as mp
import scipy as sp
import ipywidgets as iw

## Defining Feature Edges With Dihedral Angle Thresholding
### TODO: User Constraints?
Not sure how to implememt click-to-select vertices/faces, but maybe user-inputted list?

In [8]:
def feature_edges(v,f,threshold):
    edge_faces = []

    dihedral_threshold = threshold/180 * np.pi
    f_normals = igl.per_face_normals(v,f,np.ndarray([0,0]))
    edge_flaps = igl.edge_flaps(f)
    edges = edge_flaps[0]
    
    threshold_edges = []
    for i in range(edges.shape[0]):
        # find normals of faces connecting edge
        edge_face_norms = f_normals[edge_flaps[2][i]]

        # find dihedral angle between edge faces
        f1n = edge_face_norms[0] / np.linalg.norm(edge_face_norms[0])
        f2n = edge_face_norms[1] / np.linalg.norm(edge_face_norms[1])
        dihedral_angle = np.arccos(np.clip(np.dot(f1n, f2n), -1.0, 1.0))

        # add angles greater than threshold to list
        if dihedral_angle > dihedral_threshold or (-1 in edge_flaps[2][i]):
            threshold_edges.append(edges[i])
            
            # add edge faces to list
            if edge_flaps[2][i][0] != -1:
                edge_faces.append(edge_flaps[2][i][0])
            if edge_flaps[2][i][1] != -1:
                edge_faces.append(edge_flaps[2][i][1])

    threshold_edges = np.array(threshold_edges)
    return threshold_edges, edge_faces



v, f = igl.read_triangle_mesh("data/fandisk.obj")
feature_edge_list, edge_faces = feature_edges(v,f,20)

col = np.ones_like(f)
col[edge_faces, 1:] = 0

p = mp.plot(v, f, c=col, shading={"wireframe": 0})
p.add_lines(v[feature_edge_list][:,0], v[feature_edge_list][:,1], shading={"line_color": "yellow"})

Renderer(camera=PerspectiveCamera(children=(DirectionalLight(color='white', intensity=0.6, position=(2.4139499…

1

## Parametrization onto Square Map

In [9]:
def circle_to_square(x_circ,y_circ):
    x = 0.5 * np.sqrt( 2 + x_circ**2 - y_circ**2 + 2*x_circ*np.sqrt(2) ) - 0.5 * np.sqrt( 2 + x_circ**2 - y_circ**2 - 2*x_circ*np.sqrt(2) )
    y = 0.5 * np.sqrt( 2 - x_circ**2 + y_circ**2 + 2*y_circ*np.sqrt(2) ) - 0.5 * np.sqrt( 2 - x_circ**2 + y_circ**2 - 2*y_circ*np.sqrt(2) )
    x = max(min(1,x),-1)
    y = max(min(1,y),-1)
    return [x,y]

def parametrize(v,f):
    ## Find the open boundary
    bnd = igl.boundary_loop(f)
    
    ## Map the boundary to a circle, preserving edge proportions
    bnd_uv = igl.map_vertices_to_circle(v, bnd)
    
    # remap circle boundary onto square
    bnd_uv = np.array([circle_to_square(x_circ,y_circ) for [x_circ,y_circ] in bnd_uv])

    ## Harmonic parametrization for the internal vertices
    return igl.harmonic(v, f, bnd, bnd_uv, 1)


v, f = igl.read_triangle_mesh("data/fandisk.obj")
uv = parametrize(v,f)
feature_edge_list, _ = feature_edges(v,f,20)


p = mp.plot(v, f, c=np.ones_like(f), shading={"wireframe": False})
p.add_lines(v[feature_edge_list][:,0], v[feature_edge_list][:,1], shading={"line_color": "yellow"})
@iw.interact(mode=['2D','3D'])
def switch(mode):
    if mode == "3D":
        mp.plot(v, f, c=uv[:,0],shading={"wireframe": 0}, plot=p)
        p.add_lines(v[feature_edge_list][:,0], v[feature_edge_list][:,1], shading={"line_color": "yellow"})
        
    if mode == "2D":
        mp.plot(uv, f, c=np.ones_like(f), shading={"wireframe": 0, "line_width":0.2}, plot=p)
        p.add_lines(uv[feature_edge_list][:,0], uv[feature_edge_list][:,1], shading={"line_color": "black"})
        p.add_points(uv, shading={"point_size": .04})

Renderer(camera=PerspectiveCamera(children=(DirectionalLight(color='white', intensity=0.6, position=(2.4139499…

interactive(children=(Dropdown(description='mode', options=('2D', '3D'), value='2D'), Output()), _dom_classes=…

## Geometry Maps

### 1. Area Distortion Map

In [4]:
v, f = igl.read_triangle_mesh("data/fandisk.obj")
uv = parametrize(v,f)
feature_edge_list, _ = feature_edges(v,f,10)

a3d = igl.doublearea(v,f)
a2d = igl.doublearea(uv,f)

area_distortion = a3d/a2d

a = mp.plot(uv, f, c=area_distortion, shading={"wireframe": 0, "line_width":0.2})
a.add_lines(uv[feature_edge_list][:,0], uv[feature_edge_list][:,1], shading={"line_color": "black"})
a.add_points(uv, shading={"point_size": .03, "point_color": "black"})

Renderer(camera=PerspectiveCamera(children=(DirectionalLight(color='white', intensity=0.6, position=(0.0, 0.0,…

2

### 2. Curvature Maps

In [5]:
v, f = igl.read_triangle_mesh("data/fandisk.obj")
uv = parametrize(v,f)
feature_edge_list, _ = feature_edges(v,f,10)

gaussCurv = igl.gaussian_curvature(v,f)
pd1, pd2, maxCurv, minCurv = igl.principal_curvature(v, f)
totalCurv = maxCurv * maxCurv + minCurv * minCurv

a = mp.plot(uv, f, c=gaussCurv, shading={"wireframe": 0, "line_width":0.2})
a.add_lines(uv[feature_edge_list][:,0], uv[feature_edge_list][:,1], shading={"line_color": "black"})
a.add_points(uv, shading={"point_size": .03, "point_color": "black"})
@iw.interact(mode=['Gaussian','Max','Min','Total'])
def switch(mode):
    if mode == "Gaussian":
        mp.plot(uv, f, c=gaussCurv, shading={"wireframe": 0, "line_width":0.2}, plot=a)
        a.add_lines(uv[feature_edge_list][:,0], uv[feature_edge_list][:,1], shading={"line_color": "black"})
        a.add_points(uv, shading={"point_size": .03, "point_color": "black"})
        
    if mode == "Max":
        mp.plot(uv, f, c=maxCurv, shading={"wireframe": 0, "line_width":0.2}, plot=a)
        a.add_lines(uv[feature_edge_list][:,0], uv[feature_edge_list][:,1], shading={"line_color": "black"})
        a.add_points(uv, shading={"point_size": .03, "point_color": "black"})
        
    if mode == "Min":
        mp.plot(uv, f, c=minCurv, shading={"wireframe": 0, "line_width":0.2}, plot=a)
        a.add_lines(uv[feature_edge_list][:,0], uv[feature_edge_list][:,1], shading={"line_color": "black"})
        a.add_points(uv, shading={"point_size": .03, "point_color": "black"})\
        
    if mode == "Total":
        mp.plot(uv, f, c=totalCurv, shading={"wireframe": 0, "line_width":0.2}, plot=a)
        a.add_lines(uv[feature_edge_list][:,0], uv[feature_edge_list][:,1], shading={"line_color": "black"})
        a.add_points(uv, shading={"point_size": .03, "point_color": "black"})

Renderer(camera=PerspectiveCamera(children=(DirectionalLight(color='white', intensity=0.6, position=(0.0, 0.0,…

interactive(children=(Dropdown(description='mode', options=('Gaussian', 'Max', 'Min', 'Total'), value='Gaussia…

### 3. Embedding Map

In [6]:
v, f = igl.read_triangle_mesh("data/fandisk.obj")
uv = parametrize(v,f)
feature_edge_list, _ = feature_edges(v,f,10)

a = mp.plot(uv, f, c=v, shading={"wireframe": 0, "line_width":0.2})
a.add_lines(uv[feature_edge_list][:,0], uv[feature_edge_list][:,1], shading={"line_color": "black"})
a.add_points(uv, shading={"point_size": .03, "point_color": "black"})

Renderer(camera=PerspectiveCamera(children=(DirectionalLight(color='white', intensity=0.6, position=(0.0, 0.0,…

2

### 4. Face Index Map

In [7]:
import random
v, f = igl.read_triangle_mesh("data/fandisk.obj")
uv = parametrize(v,f)
feature_edge_list, _ = feature_edges(v,f,10)

def randDecimal(length):
    return float(random.uniform(0,length))/float(length)

face_index_list = []
face_index_map = {}

for i in range(f.shape[0]):
    face_col = [randDecimal(10),randDecimal(10),randDecimal(10)]
    face_index_list.append(face_col)
    while str(face_index_list[i]) in face_index_map:
        face_index_list[i] = [randDecimal(10000),randDecimal(10000),randDecimal(10000)]
    face_index_map[str(face_index_list[i])] = i
face_index_list = np.array(face_index_list)

a = mp.plot(uv, f, c=face_index_list, shading={"wireframe": 0, "line_width":0.2})
a.add_lines(uv[feature_edge_list][:,0], uv[feature_edge_list][:,1], shading={"line_color": "black"})
a.add_points(uv, shading={"point_size": .03, "point_color": "black"})

Renderer(camera=PerspectiveCamera(children=(DirectionalLight(color='white', intensity=0.6, position=(0.0, 0.0,…

2

### 5. (optional) Additional Maps
ex: normal, texture, color

In [8]:
v, f = igl.read_triangle_mesh("data/fandisk.obj")
uv = parametrize(v,f)
feature_edge_list, _ = feature_edges(v,f,10)

pvn = igl.per_vertex_normals(v,f)

a = mp.plot(uv, f, c=pvn, shading={"wireframe": 0, "line_width":0.2})
a.add_lines(uv[feature_edge_list][:,0], uv[feature_edge_list][:,1], shading={"line_color": "black"})
a.add_points(uv, shading={"point_size": .03, "point_color": "black"})

Renderer(camera=PerspectiveCamera(children=(DirectionalLight(color='white', intensity=0.6, position=(0.0, 0.0,…

2

In [9]:
from scipy.spatial import Delaunay
f_p = sp.spatial.Delaunay(uv).simplices
del_edges = igl.edges(f_p)

mp.plot(v, f_p, c=gaussCurv, shading={"wireframe": 0})


"""
@iw.interact(mode=['2Da','2Db','3Da','3Db'])
def switch(mode):
    if mode == "3Da":
        mp.plot(v, f, c=col, shading={"wireframe": 0}, plot=p)
        p.add_lines(v[feature_edge_list][:,0], v[feature_edge_list][:,1], shading={"line_color": "yellow"})
        
        p.add_lines(v[del_edges][:,0], v[del_edges][:,1], shading={"line_color": "black"})
        
    if mode == "3Db":
        mp.plot(v, f, c=col, shading={"wireframe": 1}, plot=p)
        p.add_lines(v[feature_edge_list][:,0], v[feature_edge_list][:,1], shading={"line_color": "yellow"})
            
    if mode == "2Da":
        mp.plot(v_p, f, c=col, shading={"wireframe": 0, "line_width":0.2}, plot=p)
        p.add_lines(v_p[feature_edge_list][:,0], v_p[feature_edge_list][:,1], shading={"line_color": "yellow"})
        p.add_points(v_p, shading={"point_size": .1})
        
        p.add_lines(v_p[del_edges][:,0], v_p[del_edges][:,1], shading={"line_color": "black"})

    if mode == "2Db":
        mp.plot(v_p, f, c=col, shading={"wireframe": 1, "line_width":0.2}, plot=p)
        p.add_lines(v_p[feature_edge_list][:,0], v_p[feature_edge_list][:,1], shading={"line_color": "yellow"})
        p.add_points(v_p, shading={"point_size": .1})
    """

Renderer(camera=PerspectiveCamera(children=(DirectionalLight(color='white', intensity=0.6, position=(2.4139499…

'\n@iw.interact(mode=[\'2Da\',\'2Db\',\'3Da\',\'3Db\'])\ndef switch(mode):\n    if mode == "3Da":\n        mp.plot(v, f, c=col, shading={"wireframe": 0}, plot=p)\n        p.add_lines(v[feature_edge_list][:,0], v[feature_edge_list][:,1], shading={"line_color": "yellow"})\n        \n        p.add_lines(v[del_edges][:,0], v[del_edges][:,1], shading={"line_color": "black"})\n        \n    if mode == "3Db":\n        mp.plot(v, f, c=col, shading={"wireframe": 1}, plot=p)\n        p.add_lines(v[feature_edge_list][:,0], v[feature_edge_list][:,1], shading={"line_color": "yellow"})\n            \n    if mode == "2Da":\n        mp.plot(v_p, f, c=col, shading={"wireframe": 0, "line_width":0.2}, plot=p)\n        p.add_lines(v_p[feature_edge_list][:,0], v_p[feature_edge_list][:,1], shading={"line_color": "yellow"})\n        p.add_points(v_p, shading={"point_size": .1})\n        \n        p.add_lines(v_p[del_edges][:,0], v_p[del_edges][:,1], shading={"line_color": "black"})\n\n    if mode == "2Db":\n

In [3]:
# https://github.com/10mrohit/floyd-steinberg-dithering
from math import floor
from PIL import Image

import os


class Dither():
    def __init__(self, path, algorithm=None, output=None):
        self.path = self.get_path(path)
        self.algorithm = algorithm
        self.output = output
        self.func = self.get_func(self.algorithm)
        self.func(self.path)

    def get_path(self, path):
        if path.startswith('/') and not path.startswith('~/'):
            return os.getcwd() + '/' + path
        else:
            return path

    def get_func(self, algorithm):
        return self.floyd_steinberg_dither

    def apply_threshold(self, value):
        return 255 * floor(value/128)

    def floyd_steinberg_dither(self, image_file):
        new_img = Image.open(image_file)

        new_img = new_img.convert('RGB')
        pixel = new_img.load()

        x_lim, y_lim = new_img.size

        for y in range(1, y_lim):
            for x in range(1, x_lim):
                red_oldpixel, green_oldpixel, blue_oldpixel = pixel[x, y]

                red_newpixel = self.apply_threshold(red_oldpixel)
                green_newpixel = self.apply_threshold(green_oldpixel)
                blue_newpixel = self.apply_threshold(blue_oldpixel)

                pixel[x, y] = red_newpixel, green_newpixel, blue_newpixel

                red_error = red_oldpixel - red_newpixel
                blue_error = blue_oldpixel - blue_newpixel
                green_error = green_oldpixel - green_newpixel

                if x < x_lim - 1:
                    red = pixel[x+1, y][0] + round(red_error * 7/16)
                    green = pixel[x+1, y][1] + round(green_error * 7/16)
                    blue = pixel[x+1, y][2] + round(blue_error * 7/16)

                    pixel[x+1, y] = (red, green, blue)

                if x > 1 and y < y_lim - 1:
                    red = pixel[x-1, y+1][0] + round(red_error * 3/16)
                    green = pixel[x-1, y+1][1] + round(green_error * 3/16)
                    blue = pixel[x-1, y+1][2] + round(blue_error * 3/16)

                    pixel[x-1, y+1] = (red, green, blue)

                if y < y_lim - 1:
                    red = pixel[x, y+1][0] + round(red_error * 5/16)
                    green = pixel[x, y+1][1] + round(green_error * 5/16)
                    blue = pixel[x, y+1][2] + round(blue_error * 5/16)

                    pixel[x, y+1] = (red, green, blue)

                if x < x_lim - 1 and y < y_lim - 1:
                    red = pixel[x+1, y+1][0] + round(red_error * 1/16)
                    green = pixel[x+1, y+1][1] + round(green_error * 1/16)
                    blue = pixel[x+1, y+1][2] + round(blue_error * 1/16)

                    pixel[x+1, y+1] = (red, green, blue)

        if self.output:
            new_img.save(self.output)
        else:
            new_img.show()

In [11]:
Dither("img/components.png")

In [11]:
import pygame
import igl

from pygame.locals import *

from OpenGL.GL import *
from OpenGL.GLU import *

v, f = igl.read_triangle_mesh("data/curve.off")
uv = parametrize(v,f)
v_p = np.hstack([uv, np.zeros((uv.shape[0],1))])

vertices = list(v_p)
faces = list(f)

def Cube():
    glBegin(GL_TRIANGLES)
    for face in faces:
        for vertex in face:
            glVertex3fv(tuple(vertices[vertex]))
            print(tuple(vertices[vertex]))
    glEnd()

def main():
    pygame.init()
    display = (800,600)
    pygame.display.set_mode(display, DOUBLEBUF|OPENGL)

    gluPerspective(45, (display[0]/display[1]), 0.1, 50.0)
    
    glPolygonMode( GL_FRONT_AND_BACK, GL_LINE );
    glTranslatef(0.0,0.0, -5)

    while True:
        for event in pygame.event.get():
            if event.type == pygame.QUIT:
                pygame.quit()
                quit()
        glClear(GL_COLOR_BUFFER_BIT|GL_DEPTH_BUFFER_BIT)
        Cube()
        pygame.display.flip()
        pygame.time.wait(10)

main()

(0.7523357477332342, 0.8156960205753185, 0.0)
(0.9033959429990513, 1.0, 0.0)
(0.6255617984635522, 0.7882621520611215, 0.0)
(0.8253676437888923, -0.5316867736639219, 0.0)
(0.896922360582537, -0.7099689598223614, 0.0)
(0.9193712832826023, -0.6095658989565125, 0.0)
(-0.8556184243434414, 0.5604954045320474, 0.0)
(-0.852039295162541, 0.4579199409402502, 0.0)
(-0.7764146756140846, 0.4148835457658765, 0.0)
(0.10036001826810458, 0.11841390500101895, 0.0)
(0.21393622323699027, 0.046690972943060446, 0.0)
(0.24680955872483978, 0.1610076990485756, 0.0)
(0.41820537917735845, 0.6976401468104558, 0.0)
(0.3345252190809199, 0.5938409108119987, 0.0)
(0.46651700219903725, 0.6407344486226094, 0.0)
(0.11015243881309653, 0.7905821536610066, 0.0)
(0.15635394260110833, 0.6944426576991246, 0.0)
(0.24055596686745934, 0.7508991043941472, 0.0)
(0.8084643789241203, 0.15293262014684966, 0.0)
(0.7354575328743221, 0.1237581554110519, 0.0)
(0.7667589438091522, 0.01179625266142707, 0.0)
(-0.49787680762537306, 0.7066766

KeyboardInterrupt: 